## Folium을 활용한 테러 발생 위치 시각화  
## Visualizing terrorism incident locations using Folium


### 전처리된 데이터 로드 및 지도 시각화를 위한 준비  
### Load the cleaned dataset and prepare it for map visualization


In [1]:
import pandas as pd
import folium

df = pd.read_parquet("data/interim/gtd_clean.parquet")
df.shape


(139872, 20)

### 좌표 정보가 있는 데이터만 추출하고 샘플링 수행  
### Filter records with valid coordinates and apply sampling for performance


In [2]:
# 좌표 없는 행 제거
df_map = df.dropna(subset=["latitude", "longitude"]).copy()

# 샘플링 (너무 많으면 지도 렌더링이 느려짐)
sample_n = min(3000, len(df_map))   # 오늘 제출용은 1,000~3,000이면 충분
df_map = df_map.sample(sample_n, random_state=42)

df_map.shape


(3000, 20)

### 전 세계 테러 발생 포인트 지도 생성  
### Create a global point map of terrorism incidents


In [3]:
m = folium.Map(location=[20, 0], zoom_start=2, tiles="CartoDB positron")

for _, r in df_map.iterrows():
    popup_text = f"{r['country_txt']} | {int(r['iyear'])} | {r['attacktype1_txt']}"
    folium.CircleMarker(
        location=[r["latitude"], r["longitude"]],
        radius=2,
        fill=True,
        popup=popup_text
    ).add_to(m)

m


### 마커 클러스터링을 적용하여 밀집 구간 가독성 개선  
### Improve readability by applying marker clustering for dense areas


In [4]:
from folium.plugins import MarkerCluster

m2 = folium.Map(location=[20, 0], zoom_start=2, tiles="CartoDB positron")
cluster = MarkerCluster().add_to(m2)

for _, r in df_map.iterrows():
    popup_text = f"{r['country_txt']} | {int(r['iyear'])} | {r['attacktype1_txt']}"
    folium.Marker(
        location=[r["latitude"], r["longitude"]],
        popup=popup_text
    ).add_to(cluster)

m2


### 지도 결과를 HTML 파일로 저장  
### Save the interactive map as an HTML file


In [13]:
import os
os.makedirs("outputs", exist_ok=True)

m2.save("outputs/gtd_folium_map.html")
print("saved: outputs/gtd_folium_map.html")


saved: outputs/gtd_folium_map.html
